(ch_imagewf)=
# Image workflows

## Packages

In [1]:
import ee
import geemap

try:
    ee.Initialize(project="ee-pflugmacher")
except Exception as e:
    ee.Authenticate()
    ee.Initialize(project="ee-pflugmacher")

## Set up map window

In [2]:
Map = geemap.Map(center=[53, 12], zoom=8)

## Load an image

Let’s load a Landsat-8 image from the GEE data catalog.

In [3]:
l8_img = ee.Image('LANDSAT/LC08/C02/T1_L2/LC08_193024_20180520')

We can explore the content of an ee.Image by printing it. In a python console you would use print() or getInfo(). Thanks to the eerepr package implemented in geemap, we can simply evaluate the objective in Jupyter Notebook and see the content in a nice collapsible tree.

In [4]:
l8_img

## Image properties

Images contain several types of metadata information such as band names, projection information, properties, and other metadata. To understand what methods are available for an `ee.Image` object, you may consult the [API documentation](https://developers.google.com/earth-engine/apidocs) (see Client libraries).

We can retrieve the band names of the ee.Image using the `bandNames` method.

To understand what methods are available for an `ee.Image` object, you may consult the [API documentation](https://developers.google.com/earth-engine/apidocs) (see Client libraries). For example, the `addBands()` method adds a band to an image object. You must access the method from your image object not from `ee.Image()`, i.e., `ee.Image.addBands()` does not work.

In [5]:
l8_img.bandNames()

Get a list of all metadata properties.

In [6]:
properties = l8_img.propertyNames()
properties

Get a specific metadata property:

In [7]:
band_info = l8_img.get('CLOUD_COVER')
band_info

## Image math

Image-based math operators are accessed via the created image object, e.g., image.add(), image.subtract, image.multiply(), image.divide(). Let’s calculate the NDVI from the Landsat 8 image. But first, we need to rescale the digital numbers to reflectance values using the gains and offset described in the data catalog.

In [8]:
l8_sr = l8_img.multiply(0.0000275).add(-0.2)

We can select individual bands:

In [9]:
nir = l8_sr.select("SR_B5")
red = l8_sr.select("SR_B4")

… and calculate the NDVI:

In [10]:
ndvi = nir.subtract(red) \
              .divide(nir.add(red)) \
              .rename('NDVI')
              

In [11]:
ndviVis = {"min":-1, "max":1, "palette": ['red', 'white', 'green']}
Map.addLayer(ndvi, ndviVis, 'NDVI')
Map

Map(center=[53, 12], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(chil…

## Logical operations

We can create a binary mask based on the NDVI. For example, we might want to separate areas with low NDVI (bare or sparse vegetation - but not exact) from vegetation areas.

In [12]:
veg_mask = ndvi.gt(0.4)
Map.addLayer(veg_mask, {}, 'High NDVI')

## Masking

We can apply the mask using `ee.Image.mask()` or `ee.Image.updateMask()`. For example, we can do the following to mask out bare areas:

In [13]:
veg_image = ndvi.updateMask(veg_mask)
Map.addLayer(veg_image, ndviVis, 'NDVI vegetation')

## Filter collections

Usually, we want to limit our operations to a subset of a collection. We can do that by filtering the collection by date, location, and metadata attributes.

In [14]:
l8sr = ee.ImageCollection("LANDSAT/LC08/C02/T1_L2")
geometry = ee.Geometry.Point([13.38, 52.52])

l8c = l8sr.filterDate('2016-07-01', '2017-07-08') \
          .filter(ee.Filter.lt('CLOUD_COVER', 70)) \
          .filterBounds(geometry)
l8c.count()

## Map through a collection

To apply a function to every Image in an ImageCollection use the `imageCollection.map()` method. The only argument to `map()` is a function which takes one parameter: an `ee.Image`. For example, the following code calculates the NDVI for each image. The resulting collection holds NDVI images corresponding to the Landsat image collection.

In [15]:
def calcNdvi(image):
  return image.normalizedDifference(["SR_B5", "SR_B4"]).rename("ndvi")

ndviCollection = l8c.map(calcNdvi)

# adds first image from collection to map canvas
Map.addLayer(ndviCollection.first(), ndviVis, "max NDVI")

## Reduce a collection

From the collection of NDVI images, we can now calculate aggregation statistics such as the mean, max, etc. Aggregating a collection to a single image is called reducing. Reducer's (reducing functions) are available to you in two ways: 1) via the `ee.Image` object and 2) via the `ee.Reducer` object ([help](https://developers.google.com/earth-engine/guides/reducers_intro)).

In [16]:
maxNdvi = ndviCollection.reduce(ee.Reducer.max())

medianNdvi = ndviCollection.median()

Map.addLayer(maxNdvi, {"min":0, "max":1, "palette": ['white', 'green']}, "max NDVI")

Map.addLayer(medianNdvi, {"min":0, "max":1, "palette": ['white', 'green']}, "median NDVI")
Map.centerObject(geometry, 10)

Map

Map(center=[52.52000000000001, 13.38], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=…

(sec_geeproj)=
## Projections and scale

The Earth Engine Data Catalog contains a vast amount of satellite data and geospatial data that all come in different projections and spatial resolutions. Fortunately, you do not have to worry about harmonizing between different coordinate reference systems and pixel sizes, the Earth Engine takes care of this in the background, but you need to understand some principles. **The projection and scale (pixel size) is determined by the final output rather than the input, but the actual projection is performed right in the beginning of the analysis** ([see here](https://developers.google.com/earth-engine/guides/projections)). For example, if the output is the interactive **Map display** all input data are automatically projected to Web Mercator. The scale of the output in the Map window depends on the zoom factor. If you zoom out to see the entire globe, the scale is going to be very large, i.e., the computations are performed with pixels that might be hundreds of kilometers in size. This way you can quickly generate visual results though at the expense of spatial precision. Conversely, the scale will decrease the further you zoom in the Map display. In **batch mode**, the projection and scale is set in the export function using the arguments `crs` and `scale` or `crs` and `crsTransform`. If you do not specify `crs` and `scale` the projection will default to the geographic reference system WGS84 (EPSG=4326) and a potentially large scale. For many land cover and land use applications it is recommended to specify an equal area projection. An alternative to specifying `scale` is the `crsTransform` parameter which combines information on scale and the origin of the output pixel grid.

This is useful for aligning the pixel grids of multiple outputs. The crsTransform is a list of the following format [*a*, *b*, *c*, *d*, *e*, *f*], where
- *a* is width of a pixel in map coordinates
- *b* is row rotation (typically zero)
- *c* is the x-coordinate of the upper-left corner of a pixel in the pixel grid
- *d* is the column rotation (typically zero)
- *e* is the height of a pixel (typically negative)
- *f* is the y-coordinate of the upper-left corner of a pixel in the pixel grid


## Batch environment

Recall, Earth Engine data types are server-side objects that are created and processed entirely on cloud infrastructure, and that there are two different processing environments for you to request information: 1) an interactive environment optimized for speedy and small requests, and 2) a [batch environment](https://developers.google.com/earth-engine/guides/processing_environments#batch_environment) optimized for high-latency parallel processing of large amounts of data.

Batch processing is triggered when you use an import or export function (e.g., Export.* or ee.batch.). The batch environment let’s you export large datasets to your Assets Folder or Google Cloud Storage. You can manage (view and cancel) tasks using the task manager webpage, the task tab on the online code editor, and programmatically in Python. Look [here](https://developers.google.com/earth-engine/guides/processing_environments#batch_environment) for more information.


### Export to asset

The export functions allow you to compute results in batch mode as well as save to intermediate outputs to your Earth Engine account as an [asset](https://developers.google.com/earth-engine/apidocs/export-image-toasset). The code below exports the image `maxNdvi` the asset. Note, it also specifies the projection and pixel size of 30 x 30 m ([Projections and scale](sec_geeproj)) using `crs` and `crsTransform`.

In [17]:
bounds = ee.Geometry.Polygon(
        [[[12.232347553388268, 53.243183673553276],
          [12.232347553388268, 52.0636255084833],
          [14.737230365888268, 52.0636255084833],
          [14.737230365888268, 53.243183673553276]]])

task = ee.batch.Export.image.toAsset(image=maxNdvi,
                                     description='maxNdvi', assetId='projects/ee-pflugmacher/assets/maxNdvi',
                                     region=bounds, crs= 'EPSG:3035', 
                                     crsTransform= [30, 0, 100, 0, -30, 100]
)

# start task
task.start()

### Export via geemap

In [18]:
geemap.ee_export_image(
    maxNdvi, filename='maxNDVI.tif', scale=90, 
    region=bounds, file_per_band=True
)

### Export to Google Drive

In [19]:
task = ee.batch.Export.image.toDrive(image=maxNdvi, folder='export', 
                                     description= 'landsat',
                                     region=bounds, scale=30)

# task.start()

## Task management in Python

In [ ]:
tasks = ee.batch.Task.list()
for task in tasks:
    print(f'Task ID: {task.id}, State: {task.state}, Description: {task.config.get("description", "No description")}')

In [ ]:
tasks = ee.batch.Task.list()
for task in tasks:
    print(f'Task ID: {task.id}, State: {task.state}, Description: {task.config.get("description", "No description")}')
    
for task in tasks:
    print(f'Task ID: {task.id}, State: {task.state}, Description: {task.config.get("description", "No description")}')
    if task.state == 'FAILED':
        print(f'Error: {task.error_message}')

## Reading

* [GEE: Get started](https://developers.google.com/earth-engine/guides/getstarted)
* [Cloud-Based Remote Sensing with Google Earth Engine: 
Fundamentals and Applications (Book)](https://link.springer.com/book/10.1007/978-3-031-26588-4)
* [Notebook examples by Qiusheng Wu](https://github.com/giswqs/earthengine-py-notebooks)
* [eemont package: image pre-processing and processing functions](https://github.com/davemlz/eemont)